In [1]:
# Importing required libraries
import pandas as pd
import ast
import re
import sys

from helper_functions.helpers import clean, structure_conversation_spacy, structure_conversation, Parse_spacy, Parse
from resolution_helpers.object_phrase_resolution import extract_head_verb_object
from resolution_helpers.append_resolved_phrase import append_resolved_vp
from resolution_helpers.append_missing_aux import find_missing_aux_verb
from detect_and_resolve_vpe import detect_resolve_vpe_conversation, detect_resolve_vpe_conversation_spacy
from compare_with_annotations import compare_head_verb, compare_ellided_obj_parent

import json

# Reading Annotated File
annotated_df = pd.read_excel("./Data/train.xlsx")

# Currently Checking Accuracy on Test/Train
text = annotated_df['english'].tolist()
annotations = annotated_df[annotated_df.columns[3]].tolist()
obj_only_ellipsis_annotations = annotated_df[annotated_df.columns[4]].tolist()

# Removing empty lines from the list
for line in text:
    if(line == '' or line == '\n'):
        text.remove(line)

# Counting lines and number of cases where ellipsis is detected and where it isn't detected
cases_ellipsis = 0
cases_no_ellipsis = 0

error_conversations = []

detect_resolve_output_file = open("./Outputs/detect_resolve_output_annotated.txt", "w+")

corr_count = 0
ann_count = 0

conversation_final_vpe_list = []

2023-04-30 14:04:50.247967: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-04-30 14:04:50.248014: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining 

In [2]:
# Running it for all sentences in our list
for index, conversation in enumerate(text):
   
    print(str(index) + ") ", end = " ", file = detect_resolve_output_file)
    print(conversation, end = "\n\n", file = detect_resolve_output_file)

    temp_entry_output_storage_file = open("./Outputs/TempConversationalOutput/train_entry_" + str(index) + ".txt", "w")

    print("Entry - %d\n" %(index), file = temp_entry_output_storage_file)
    print("Scoring in STANFORD\n", file = temp_entry_output_storage_file)
    print("Scoring in STANFORD\n", file = detect_resolve_output_file)
    vpe_conversation_stanford = detect_resolve_vpe_conversation(clean(conversation), detect_resolve_output_file, temp_entry_output_storage_file)
    
    print("Scoring in SPACY\n", file = temp_entry_output_storage_file)
    print("Scoring in SPACY\n", file = detect_resolve_output_file)
    vpe_conversation_spacy = detect_resolve_vpe_conversation_spacy(clean(conversation), detect_resolve_output_file, temp_entry_output_storage_file)
    
    detected_vpe_cases_stanford = []
    for output_arr in vpe_conversation_stanford:
        if output_arr != []:
            detected_vpe_cases_stanford.append(output_arr)
            
    detected_vpe_cases_spacy = []
    for output_arr in vpe_conversation_spacy:
        if output_arr != []:
            detected_vpe_cases_spacy.append(output_arr)
    
    # Taking only those detections where both the parsers detected VPE in the conversation
    final_vpe_list = []
    
    for vpe_dict_stanford in detected_vpe_cases_stanford:
        for vpe_dict_spacy in detected_vpe_cases_spacy:
            if vpe_dict_stanford['category'] == vpe_dict_spacy['category'] and vpe_dict_stanford['site'] == vpe_dict_spacy['site'] and vpe_dict_stanford['sen_index'] == vpe_dict_spacy['sen_index']:
                
                # If Main verb is resolved and both Stanford Spacy head verb resolutions match then choose any since they both are the same
                if vpe_dict_stanford['resolved_head_verb'] is not None and vpe_dict_spacy['resolved_head_verb'] is not None and vpe_dict_stanford['resolved_head_verb'] == vpe_dict_spacy['resolved_head_verb']:
                    final_vpe_list.append(vpe_dict_stanford)
                # If Main verb is resolved and Stanford Spacy head verb resolutions don't match then giving preference to Spacy
                if vpe_dict_stanford['resolved_head_verb'] is not None and vpe_dict_spacy['resolved_head_verb'] is not None and vpe_dict_stanford['resolved_head_verb'] != vpe_dict_spacy['resolved_head_verb']:
                    final_vpe_list.append(vpe_dict_spacy)
                # If Main verb is resolved for Spacy but not for Stanford then choose any since they Spacy
                if vpe_dict_stanford['resolved_head_verb'] is None and vpe_dict_spacy['resolved_head_verb'] is not None:
                    final_vpe_list.append(vpe_dict_spacy)
                # If Main verb is resolved for Stanford but not for Spacy then choose any since they Stanford
                if vpe_dict_stanford['resolved_head_verb'] is not None and vpe_dict_spacy['resolved_head_verb'] is None:
                    final_vpe_list.append(vpe_dict_stanford)
                # If Main verb is not resolved for neither of them it implies Only the Object child is ellided and if the Ellided Object child's parents matches then choose any since they are the same. 
                # Note that matched Ellided Object Child's parent could also be None which would imply we couldn't resolve the ellipsis successfully
                if vpe_dict_stanford['resolved_head_verb'] is None and vpe_dict_spacy['resolved_head_verb'] is None and vpe_dict_stanford['ellided_obj_child_parent_verb'] == vpe_dict_spacy['ellided_obj_child_parent_verb']:
                    final_vpe_list.append(vpe_dict_spacy)
                # If Main verb is not resolved for neither of them it implies Only the Object child is ellided and if the Ellided Object child's parents don't match then choose Spacy
                if vpe_dict_stanford['resolved_head_verb'] is None and vpe_dict_spacy['resolved_head_verb'] is None and vpe_dict_stanford['ellided_obj_child_parent_verb'] != vpe_dict_spacy['ellided_obj_child_parent_verb']:
                    final_vpe_list.append(vpe_dict_spacy)
                

    # To check category wise performance select category from 1-5 or keep it None
    comparison_category = None
    
    structured_conversation = structure_conversation_spacy(clean(conversation))[0]

    corr_count, ann_count, print_flag_pure = compare_head_verb(final_vpe_list, annotations[index], corr_count, ann_count, comparison_category, temp_entry_output_storage_file)
    corr_count, ann_count, print_flag_obj_only = compare_ellided_obj_parent(structured_conversation, final_vpe_list, obj_only_ellipsis_annotations[index], corr_count, ann_count, comparison_category, temp_entry_output_storage_file)
    
    final_vpe_list = extract_head_verb_object(final_vpe_list, structure_conversation_spacy(clean(conversation)))
    final_vpe_list = find_missing_aux_verb(final_vpe_list, structure_conversation_spacy(clean(conversation)))
    
    conversation_final_vpe_list.append(final_vpe_list)
    
    print("\nFINAL VPE\n", file = temp_entry_output_storage_file)
    print(final_vpe_list, file = temp_entry_output_storage_file)
    print("\nFINAL VPE\n", file = detect_resolve_output_file)
    print(final_vpe_list, file = detect_resolve_output_file)
    
    print("\nACTUAL ANNOTATIONS\n", file = temp_entry_output_storage_file)
    print(annotations[index], file = temp_entry_output_storage_file)
    print("\nACTUAL ANNOTATIONS\n", file = detect_resolve_output_file)
    print(annotations[index], file = detect_resolve_output_file)
    
    if ann_count>0:
        print("\nCURRENT ACCURACY ==> %d/%d = %f\n" % (corr_count, ann_count, corr_count/ann_count), file = temp_entry_output_storage_file)
    
    print("================================= \n\n", file = temp_entry_output_storage_file)
    
    print("================================= \n\n", file = detect_resolve_output_file)
    
    temp_entry_output_storage_file.close()
    
#     if print_flag_pure or print_flag_obj_only:
    temp_entry_read_file = open("./Outputs/TempConversationalOutput/train_entry_" + str(index) + ".txt", "r")
    erroneous_entry = temp_entry_read_file.read()
    print(erroneous_entry)
    temp_entry_read_file.close()
    
detect_resolve_output_file.close()

Entry - 0

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[1, 2, 3]
{0: 0}
[{1: 0, 3: 0}, {}, {2: 0}]


AFTER VERB LIST FILTERING
[1, 2, 3]
{}
[{1: 0}, {}, {2: 0}]


Prev 1 - 1 NUMBER + 1
Prev 3 - 2 NUMBER + 1
AFTER NOMINAL SUBJECT BASED SCORING
[1, 2, 3]
{}
[{1: 1}, {}, {2: 1}]


AFTER COMP CLAUSE BASED SCORING
[1, 2, 3]
{}
[{1: 1}, {}, {2: 1}]


AFTER AUX BASED SCORING
[1, 2, 3]
{}
[{1: 1}, {}, {2: 1}]


AFTER BACKTRACKING BASED SCORING
[1, 2, 3]
{}
[{1: 1}, {}, {2: 1}]


AFTER ADDING SCORE MULTIPLIERS
[1, 2, 3]
{}
[{1: 0.65}, {}, {2: 1}]
-----------------------------


BEFORE VERB LIST FILTERING
[4, 5, 6]
{0: 0, 3: 0, 5: 0}
[{0: 0}, {1: 0, 4: 0, 5: 0, 7: 0}, {1: 0}]


AFTER VERB LIST FILTERING
[4, 5, 6]
{}
[{0: 0}, {1: 0, 5: 0, 7: 0}, {}]


Prev 4 - 0 SAME SUBJECT FP SP NO SWITCH + 2
Prev 5 - 1 NUMBER + 1
Prev 5 - 1 FP SP SWITCH + 1
Prev 5 - 5 NUMBER + 1
Prev 5 - 5 FP SP SWITCH + 1
Prev 5 - 7 NUMBER + 1
Prev 5 - 7 FP SP SWITCH + 1
AFTER NOMINAL SUBJECT BASED SCORING
[4, 5, 6]
{}
[{

Entry - 4

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[7, 8, 9]
{3: 0, 7: 0}
[{2: 0, 5: 0, 10: 0, 12: 0}, {1: 0}, {0: 0, 2: 0}]


AFTER VERB LIST FILTERING
[7, 8, 9]
{}
[{2: 0, 5: 0, 12: 0}, {}, {0: 0, 2: 0}]


Prev 7 - 12 PASSIVITY - 2
Prev 7 - 12 TP - 1
Prev 9 - 2 FP SP SWITCH + 1
AFTER NOMINAL SUBJECT BASED SCORING
[7, 8, 9]
{}
[{2: 0, 5: 0, 12: -3}, {}, {0: 0, 2: 1}]


AFTER COMP CLAUSE BASED SCORING
[7, 8, 9]
{}
[{2: 0, 5: -1, 12: -4}, {}, {0: 0, 2: 1}]


AFTER AUX BASED SCORING
[7, 8, 9]
{}
[{2: 0, 5: -1, 12: -4}, {}, {0: 0, 2: 2}]


AFTER BACKTRACKING BASED SCORING
[7, 8, 9]
{}
[{2: 0, 5: -1, 12: -4}, {}, {0: 0, 2: 2}]


AFTER ADDING SCORE MULTIPLIERS
[7, 8, 9]
{}
[{2: 0.0, 5: -0.65, 12: -2.6}, {}, {0: 0, 2: 2}]
-----------------------------


Scoring in SPACY

BEFORE VERB LIST FILTERING
[7, 8, 9]
{3: 0, 7: 0}
[{2: 0, 5: 0, 10: 0, 12: 0}, {1: 0}, {0: 0, 2: 0}]


AFTER VERB LIST FILTERING
[7, 8, 9]
{}
[{2: 0, 5: 0, 12: 0}, {}, {0: 0, 2: 0}]


Prev 7 - 12 PASSIVITY - 2
Prev 7

Entry - 9

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[0]
{1: 0, 6: 0, 8: 0}
[{3: 0}]


AFTER VERB LIST FILTERING
[0]
{}
[{3: 0}]


Prev 0 - 3 NUMBER + 1
Prev 0 - 3 FP SP SWITCH + 1
AFTER NOMINAL SUBJECT BASED SCORING
[0]
{}
[{3: 2}]


AFTER COMP CLAUSE BASED SCORING
[0]
{}
[{3: 2}]


AFTER AUX BASED SCORING
[0]
{}
[{3: 2}]


AFTER BACKTRACKING BASED SCORING
[0]
{}
[{3: 2}]


AFTER ADDING SCORE MULTIPLIERS
[0]
{}
[{3: 2}]
-----------------------------


Scoring in SPACY

BEFORE VERB LIST FILTERING
[0]
{1: 0, 6: 0, 8: 0}
[{3: 0}]


AFTER VERB LIST FILTERING
[0]
{}
[{3: 0}]


Prev 0 - 3 NUMBER + 1
Prev 0 - 3 FP SP SWITCH + 1
AFTER NOMINAL SUBJECT BASED SCORING
[0]
{}
[{3: 2}]


AFTER COMP CLAUSE BASED SCORING
[0]
{}
[{3: 2}]


AFTER AUX BASED SCORING
[0]
{}
[{3: 2}]


AFTER BACKTRACKING BASED SCORING
[0]
{}
[{3: 2}]


AFTER ADDING SCORE MULTIPLIERS
[0]
{}
[{3: 2}]
-----------------------------



COMPARING PURE ELLIPSIS RESOLUTIONS WITH ITS ANNOTATIONS

[['finish', "That's all right

Entry - 18

Scoring in STANFORD

Scoring in SPACY


FINAL VPE

[]

ACTUAL ANNOTATIONS

[2, 1, 1, 1, 1, 1, 6, "Yes , <<I have done this>> for the last 20 years ."]

CURRENT ACCURACY ==> 15/15 = 1.000000




Entry - 19

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[0, 1, 2]
{4: 0}
[{1: 0}, {1: 0, 5: 0}, {1: 0, 4: 0, 5: 0}]


AFTER VERB LIST FILTERING
[0, 1, 2]
{}
[{1: 0}, {}, {1: 0, 4: 0, 5: 0}]


Prev 0 - 1 NUMBER + 1
Prev 0 - 1 FP SP SWITCH + 1
Prev 2 - 1 NUMBER + 1
Prev 2 - 1 FP SP SWITCH + 1
Prev 2 - 5 NUMBER + 1
Prev 2 - 5 FP SP SWITCH + 1
AFTER NOMINAL SUBJECT BASED SCORING
[0, 1, 2]
{}
[{1: 2}, {}, {1: 2, 4: 0, 5: 2}]


AFTER COMP CLAUSE BASED SCORING
[0, 1, 2]
{}
[{1: 2}, {}, {1: 2, 4: 0, 5: 2}]


AFTER AUX BASED SCORING
[0, 1, 2]
{}
[{1: 2}, {}, {1: 2, 4: 0, 5: 3}]


AFTER BACKTRACKING BASED SCORING
[0, 1, 2]
{}
[{1: 2}, {}, {1: 2, 4: 0, 5: 3}]


AFTER ADDING SCORE MULTIPLIERS
[0, 1, 2]
{}
[{1: 1.3}, {}, {1: 2, 4: 0, 5: 3}]
-----------------------------


Scoring in SPACY

BE

Entry - 24

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[0, 1]
{1: 0}
[{3: 0}, {1: 0}]


AFTER VERB LIST FILTERING
[0, 1]
{}
[{3: 0}, {1: 0}]


Prev 1 - 1 NUMBER + 1
Prev 1 - 1 FP SP SWITCH + 1
AFTER NOMINAL SUBJECT BASED SCORING
[0, 1]
{}
[{3: 0}, {1: 2}]


AFTER COMP CLAUSE BASED SCORING
[0, 1]
{}
[{3: 0}, {1: 2}]


AFTER AUX BASED SCORING
[0, 1]
{}
[{3: 0}, {1: 2}]


AFTER BACKTRACKING BASED SCORING
[0, 1]
{}
[{3: 0}, {1: 2}]


AFTER ADDING SCORE MULTIPLIERS
[0, 1]
{}
[{3: 0.0}, {1: 2}]
-----------------------------


Scoring in SPACY

BEFORE VERB LIST FILTERING
[0, 1]
{1: 0}
[{3: 0}, {1: 0}]


AFTER VERB LIST FILTERING
[0, 1]
{}
[{3: 0}, {1: 0}]


Prev 1 - 1 NUMBER + 1
Prev 1 - 1 FP SP SWITCH + 1
AFTER NOMINAL SUBJECT BASED SCORING
[0, 1]
{}
[{3: 0}, {1: 2}]


AFTER COMP CLAUSE BASED SCORING
[0, 1]
{}
[{3: 0}, {1: 2}]


AFTER AUX BASED SCORING
[0, 1]
{}
[{3: 0}, {1: 2}]


AFTER BACKTRACKING BASED SCORING
[0, 1]
{}
[{3: 0}, {1: 2}]


AFTER ADDING SCORE MULTIPLIERS
[0, 1]
{}
[{3:

...

Entry - 795

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[0, 1]
{3: 0, 5: 0, 9: 0}
[{1: 0}, {1: 0, 2: 0, 4: 0}]


AFTER VERB LIST FILTERING
[0, 1]
{3: 0, 5: 0}
[{1: 0}, {2: 0}]


3 NUMBER + 1
Prev 0 - 1 NUMBER + 1
Prev 0 - 1 TP - 1
Prev 1 - 2 FP SP NONSWITCH + 1
AFTER NOMINAL SUBJECT BASED SCORING
[0, 1]
{3: 1, 5: 0}
[{1: 0}, {2: 1}]


AFTER COMP CLAUSE BASED SCORING
[0, 1]
{3: 1, 5: 0}
[{1: 0}, {2: 1}]


AFTER AUX BASED SCORING
[0, 1]
{3: 1, 5: 0}
[{1: 0}, {2: 1}]


AFTER BACKTRACKING BASED SCORING
[0, 1]
{3: 1, 5: 1}
[{1: 0}, {2: 1}]


AFTER ADDING SCORE MULTIPLIERS
[0, 1]
{3: 1, 5: 1}
[{1: 0.0}, {2: 1}]
-----------------------------


BEFORE VERB LIST FILTERING
[7, 8, 9]
{0: 0, 6: 0}
[{1: 0}, {1: 0, 3: 0, 6: 0}, {2: 0}]


AFTER VERB LIST FILTERING
[7, 8, 9]
{}
[{}, {1: 0, 3: 0, 6: 0}, {2: 0}]


Prev 8 - 3 NUMBER + 1
Prev 8 - 6 NUMBER + 1
Prev 8 - 6 TP - 1
AFTER NOMINAL SUBJECT BASED SCORING
[7, 8, 9]
{}
[{}, {1: 0, 3: 1, 6: 0}, {2: 0}]


AFTER COMP CLAUSE BASED SCORING
[7, 8, 9]

Entry - 797

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[2, 3, 4]
{0: 0, 2: 0}
[{1: 0}, {1: 0, 3: 0, 4: 0, 5: 0}, {2: 0, 3: 0, 6: 0}]


AFTER VERB LIST FILTERING
[2, 3, 4]
{}
[{}, {1: 0, 3: 0, 5: 0}, {2: 0, 3: 0}]


Prev 3 - 3 SAME SUBJECT TP + 2
Prev 4 - 2 SAME SUBJECT TP + 2
AFTER NOMINAL SUBJECT BASED SCORING
[2, 3, 4]
{}
[{}, {1: 0, 3: 2, 5: 0}, {2: 2, 3: 0}]


AFTER COMP CLAUSE BASED SCORING
[2, 3, 4]
{}
[{}, {1: 0, 3: 2, 5: 0}, {2: 2, 3: 0}]


AFTER AUX BASED SCORING
[2, 3, 4]
{}
[{}, {1: 0, 3: 2, 5: 0}, {2: 2, 3: 0}]


AFTER BACKTRACKING BASED SCORING
[2, 3, 4]
{}
[{}, {1: 0, 3: 2, 5: 0}, {2: 2, 3: 0}]


AFTER ADDING SCORE MULTIPLIERS
[2, 3, 4]
{}
[{}, {1: 0.0, 3: 1.6, 5: 0.0}, {2: 2, 3: 0}]
-----------------------------


BEFORE VERB LIST FILTERING
[3, 4, 5]
{3: 0}
[{1: 0, 3: 0, 4: 0, 5: 0}, {2: 0, 3: 0, 6: 0}, {0: 0, 2: 0}]


AFTER VERB LIST FILTERING
[3, 4, 5]
{3: 0}
[{1: 0, 3: 0, 5: 0}, {2: 0, 3: 0}, {0: 0, 2: 0}]


Prev 3 - 1 NUMBER + 1
Prev 3 - 1 FP SP SWITCH + 1
Prev

Entry - 799

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[0, 1, 2]
{5: 0}
[{1: 0}, {1: 0}, {5: 0, 7: 0}]


AFTER VERB LIST FILTERING
[0, 1, 2]
{}
[{}, {}, {7: 0}]


Prev 2 - 7 SAME SUBJECT TP + 2
AFTER NOMINAL SUBJECT BASED SCORING
[0, 1, 2]
{}
[{}, {}, {7: 2}]


AFTER COMP CLAUSE BASED SCORING
[0, 1, 2]
{}
[{}, {}, {7: 2}]


AFTER AUX BASED SCORING
[0, 1, 2]
{}
[{}, {}, {7: 3}]


AFTER BACKTRACKING BASED SCORING
[0, 1, 2]
{}
[{}, {}, {7: 3}]


AFTER ADDING SCORE MULTIPLIERS
[0, 1, 2]
{}
[{}, {}, {7: 3}]
-----------------------------


BEFORE VERB LIST FILTERING
[10, 11, 12]
{4: 0}
[{3: 0, 5: 0, 8: 0}, {4: 0, 6: 0}, {6: 0, 10: 0, 17: 0}]


AFTER VERB LIST FILTERING
[10, 11, 12]
{}
[{3: 0, 5: 0, 8: 0}, {4: 0, 6: 0}, {6: 0, 10: 0, 17: 0}]


Prev 10 - 3 SAME SUBJECT TP + 2
Prev 11 - 4 SAME SUBJECT TP + 2
AFTER NOMINAL SUBJECT BASED SCORING
[10, 11, 12]
{}
[{3: 2, 5: 0, 8: 0}, {4: 2, 6: 0}, {6: 0, 10: 0, 17: 0}]


AFTER COMP CLAUSE BASED SCORING
[10, 11, 12]
{}
[{3: 2, 5: 0, 8: 0}, {4:

Entry - 802

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[1, 2, 3]
{2: 0, 7: 0}
[{}, {1: 0}, {2: 0}]


AFTER VERB LIST FILTERING
[1, 2, 3]
{}
[{}, {}, {}]


AFTER NOMINAL SUBJECT BASED SCORING
[1, 2, 3]
{}
[{}, {}, {}]


AFTER COMP CLAUSE BASED SCORING
[1, 2, 3]
{}
[{}, {}, {}]


AFTER AUX BASED SCORING
[1, 2, 3]
{}
[{}, {}, {}]


AFTER BACKTRACKING BASED SCORING
[1, 2, 3]
{}
[{}, {}, {}]


Scoring in SPACY

BEFORE VERB LIST FILTERING
[1, 2, 3]
{2: 0, 7: 0}
[{}, {1: 0}, {2: 0}]


AFTER VERB LIST FILTERING
[1, 2, 3]
{}
[{}, {}, {}]


AFTER NOMINAL SUBJECT BASED SCORING
[1, 2, 3]
{}
[{}, {}, {}]


AFTER COMP CLAUSE BASED SCORING
[1, 2, 3]
{}
[{}, {}, {}]


AFTER AUX BASED SCORING
[1, 2, 3]
{}
[{}, {}, {}]


AFTER BACKTRACKING BASED SCORING
[1, 2, 3]
{}
[{}, {}, {}]



COMPARING OBJECT ONLY ELLIPSIS RESOLUTIONS WITH ITS ANNOTATIONS

[]
[]

0 resolutions out of 0 are correct.

FINAL VPE

[{'category': 1, 'site': 7, 'licensor': 'is', 'lemmatized_licensor': 'be', 'sen_index': 4, 'resolve

Entry - 807

Scoring in STANFORD

BEFORE VERB LIST FILTERING
[0, 1, 2]
{3: 0}
[{1: 0, 3: 0}, {1: 0}, {0: 0, 2: 0}]


AFTER VERB LIST FILTERING
[0, 1, 2]
{}
[{3: 0}, {}, {2: 0}]


Prev 0 - 3 NUMBER + 1
Prev 2 - 2 SAME SUBJECT TP + 2
AFTER NOMINAL SUBJECT BASED SCORING
[0, 1, 2]
{}
[{3: 1}, {}, {2: 2}]


AFTER COMP CLAUSE BASED SCORING
[0, 1, 2]
{}
[{3: 1}, {}, {2: 2}]


AFTER AUX BASED SCORING
[0, 1, 2]
{}
[{3: 2}, {}, {2: 3}]


AFTER BACKTRACKING BASED SCORING
[0, 1, 2]
{}
[{3: 2}, {}, {2: 3}]


AFTER ADDING SCORE MULTIPLIERS
[0, 1, 2]
{}
[{3: 1.3}, {}, {2: 3}]
-----------------------------


Scoring in SPACY

BEFORE VERB LIST FILTERING
[0, 1, 2]
{3: 0}
[{1: 0, 3: 0}, {1: 0}, {0: 0, 2: 0}]


AFTER VERB LIST FILTERING
[0, 1, 2]
{}
[{3: 0}, {}, {2: 0}]


Prev 0 - 3 NUMBER + 1
Prev 2 - 2 SAME SUBJECT TP + 2
AFTER NOMINAL SUBJECT BASED SCORING
[0, 1, 2]
{}
[{3: 1}, {}, {2: 2}]


AFTER COMP CLAUSE BASED SCORING
[0, 1, 2]
{}
[{3: 1}, {}, {2: 2}]


AFTER AUX BASED SCORING
[0, 1, 2]
{}
[{3: 2}

In [3]:
for index, conversation in enumerate(text):
    print(str(index) + ") ", end = "\n")
    cleaned_text = re.sub("__eou__", "", text[index])
    cleaned_text = re.sub(' +', ' ', cleaned_text)
    cleaned_text = cleaned_text.strip()
    print(cleaned_text, end = "\n\n")
    resolved_conversation, resolved_conversation_parsed = append_resolved_vp(conversation_final_vpe_list[index], clean(text[index]))
    print(resolved_conversation, end = "\n\n=================================\n\n")

0) 
Isn ’ t he the best instructor ? I think he ’ s so hot . Wow ! I really feel energized . Do you ? I swear , I ' m going to kill you for this . What ’ s wrong ? Didn ' t you think it was fun ? ! Oh , yeah ! I had a blast ! I love sweating like a pig with a bunch of pot bellies who all smell bad . Sorry , I ’ m just not into this health kick . Oh , no , get off it . It wasn ’ t such a killer class . You just have to get into it . Like they say , no pain , no gain . I am wiped out . Thank you . Look , next time get yourself some comfy shoes . You ’ re gonna come back again with me , aren ’ t you ? Never ! But thank you for inviting me . Come on . You ’ ll feel better after we hit the showers .

Isn't he the best instructor ? I think he's so hot . Wow ! I really feel energized . Do you feel energized ? I swear , I'm going to kill you for this . What's wrong ? Didn't you think it was fun ? ! Oh , yeah ! I had a blast ! I love sweating like a pig with a bunch of pot bellies who all smell

Where are you going ? To the office . I'll be right back .


13) 
Could you babysit for me tonight ? I'd be glad to .

Could you babysit for me tonight ? I 'd be glad to babysit for you .


14) 
Do you play mahjong ? Once in a while .

Do you play mahjong ? Once in a while .


15) 
Get up , you lazybones ! Just a minute .

Get up , you lazybones ! Just a minute .


16) 
Shall we start decorating the bedroom ? I've already started . When ? This afternoon .

Shall we start decorating the bedroom ? I've already started . When ? This afternoon .


17) 
You just ran a red light . Did I ?

You just ran a red light . Did I ran a red light ?


18) 
First you add the washing powder then you add the clothes . I take it you've done this before ? Yes , for the last 20 years . Good .

First you add the washing powder then you add the clothes . I take it you've done this before ? Yes , for the last 20 years . Good .


19) 
I stayed at Bob's last night . I was worried where you were . I guess I shoul

It's your turn now , Helen . okay . I'm coming . This is your song . I picked it for you . Thank you . You are so considerate . Push the red button on the mike to turn it on . okay . This key is too high for me . I think it's a piece of cake for you . okay . Let me have a try ... Well done ! I hope I can sing as well as you can sing one day . Thank you . I 'm sure you will sing . I hope so . Thank you for saying so .


33) 
Who is the next one ? It's Peter's turn . Give the mike to him . OK . Be quiet . He is singing . I thought he only liked to listen ! So did I . He has a really good voice ! Yes , he sings wonderfully .

Who is the next one ? It's Peter's turn . Give the mike to him . okay . Be quiet . He is singing . I thought he only liked to listen ! So did thought I . He has a really good voice ! Yes , he sings wonderfully .


34) 
What kind of music do you like ? I like popular music best . Me too . Who is your favorite singer ? Qi In is . Do you know this song ? Yes , I like it

We can't go that way , the road is blocked for the next few days . Oh , that's right . They're filming a movie up there , aren't they ? Some high speed chase scene , I think . I wonder how all the businesses in the area feel about that . I think that they get a pretty good payoff . The movie company has to pay them ? I don't know about all of that , but think about it , their business gets free publicity ! Oh , yeah , they get to be in a movie for the whole world to see !


49) 
Who ate the cookies that were sitting here ? I did , Mom . Shame on you . I was saving them for your brother .

Who ate the cookies that were sitting here ? I did ate the cookies , Mom . Shame on you . I was saving them for your brother .


50) 
What do you think about all the different diets that people go on ? I don't think dieting is good for you . It's much better to eat a balanced diet and to never get overweight to begin with ! But what do you think about people who are obese ? What should they do to lose

Do you remember what the ratings of movies stand for ? Yes , G stands for General Audiences , PG means Parental Guidance suggested , R is restricted to audiences under 18 and X means explicit content . Does anyone pay any attention to those ratings anymore ? Remember when we were kids ? Theaters wouldn't let kids in to PG moves without a parent . I remember that I never saw an X moves even displayed . Now with video rentals it's all a personal matter . Yea , I never see theaters turn people away for their age anymore either . Now we have to make a choice about what we will see and what we won't make a choice about .


59) 
( A stranger stops to help ) Everything OK ? No ! My tour bus got a speeding ticket not ten minutes ago . Now my engine is on fire ! I think that's just steam . Your engine's overheated . Do you know a lot about cars ? A little bit . I'll take a look if you want me to . Please . Thank you so much for stopping . Yeah , she's hot . Radiator's leaking . Looks like you w

...

I'm Miss Sherman . What seems to be the problem ? Well , apparently I'Ve run up quite a bill . I was under the impression that the Junior Executive Holiday Package only cost 250 dollars per night . I'Ve just been informed that it's actually 500 dollars That's true . For the Junior Executive Room ... three nights ... yes , your bill should be $ 1,500 But I definitely was led to believe that a three-night stay would be $ 750 . The advertised rate is based on double occupancy . When I booked the room , your staff didn't mention this . And the brochure and your promotional mailings do not mention that . Are you quite sure ? Yes , I am sure . Have a look . I see . I had no idea our advertising was so misleading . It is here , but it's in the fine print on the last page . Perhaps you could arrange to provide me with a new bill that reflects the advertised rate . Normally I couldn't do that . But under the circumstances , I'll see what I can arrange.Customer satisfaction is our primary aim . 

is everything alright ? yes , everything is fine . what took so long ? I thought your flight was supposed to arrive 3 hours ago ! didn't they announce that our flight was delayed ? I didn't hear anything about a delay . I thought everything was running on time . What happened ? we boarded the plane on time , but then we were held up for almost an hour due to a maintenance problem . then what ? Your plane was three hours late ! we finally took off , but about 30 minutes later , the captain came on the loudspeaker to warn us that there would be some bad turbulence for most of the flight . turbulence is pretty normal , isn't it ? yes , but this was the worst turbulence I'd ever experienced in my life ! Everyone started getting sick . The flight attendants had to stay in their seats . The captain decided to land early . so where did you land ? we landed in Southampton and waited an hour for the storms to pass and then took off again . that sounds like a nightmare ! it wasn't too bad . At l

hey , Tom , did you enjoy your lunch ? oh , don't mention it . It was terrible . what'the matter ? the food station was as crowded as usual . I waited for 20 minutes for my sandwich , and when I finally got it the chicken was underdone . I see . You simply can't blame the server for this . yes , I know . Fast food is so popular in this district . that's true . anyway , how was your such , Catherine ? it was good . I brought lunch from home today . you did ? I thought you must feel right at home here as we get as many fast food restaurants as you do feel in America . well , I personally don't like then because i don't believe they are healthy . i guess you're right . More often than not , people go there only for convenience . The foods may taste good , but generally speaking , they are high in calories , salt and fat . yes . I am wondering that you must believe fast food is your lifestyle , don't you ? you bet . Almost all top brands such as McDonald's and KFC are from America . well ,

What do you think of this one ? Eh , so so . And this one ? Too flashy ? Nah , not too flashy . Hug ! And this sweater from my aunt ? Isn't it hideous ? I guess . Are you even listening ? I'm trying to have a conversation with you . And I'm trying to watch the game , but you're yapping on about your new clothes ! Well I have to decide which gifts to keep and which to exchange for better ones when I go to the Boxing Day sales this afternoon ! Well could you do me the favor of making this quick ? It's the third quarter and you'Ve been blabbering on since the first ! Oh , your precious game . You watch the same game every year , and each year your beloved hometown team loses by at least three goals ! You didn't just insult the Sals-bury Seals , did you ? Why don't you just go and return all of those stupid clothes and not come back until the sales are over ? I might come just ! Enjoy your stupid game ! And Merry Christmas ! Merry Christmas !


794) 
What are you doing ? Look at me . I loo

Hurry up , get in . I'm in , let's go ! okay , make a left here ...no wait , I meant make a right . Come on , speed up ! Geez ! What's the rush ? Don't worry about it , just drive . Oh , no , the light is about to change ...step on it ! Are you nuts ! I'm not going to run a red light ! Whatever . Just turn right here .... The freeway will be packed at this hour .... let's take a side street.Go on ! Get out of our way ! Move , move ! What's your problem ! Geez . Having a fit is not going to help ! Here , I know a short cut ... just go down here , and we'll cut though Ashburn Heights . Let's go , let's go ! Watch out for that lady ! I 'm going as fast as I can going ! Yes ! We made it . 5:58 , just before the library closes . You're such a geek !


802) 
Morning . Hi there Mr . Anderson ! How are you on this fine morning ? Fine , thank you . It sure is cold this morning , isn ’ t it ? I barely even get out of bed ! Yeah . It ’ s pretty cold , alright . Did you catch the news this morning